In [1]:
# Import packages
library(rstan)
library(coda)
library(parallel)
library(Bessel)

Loading required package: StanHeaders
Loading required package: ggplot2
Registered S3 methods overwritten by 'ggplot2':
  method         from 
  [.quosures     rlang
  c.quosures     rlang
  print.quosures rlang
rstan (Version 2.19.2, GitRev: 2e1f913d3ca3)
For execution on a local, multicore CPU with excess RAM we recommend calling
options(mc.cores = parallel::detectCores()).
To avoid recompilation of unchanged Stan programs, we recommend calling
rstan_options(auto_write = TRUE)
For improved execution time, we recommend calling
Sys.setenv(LOCAL_CPPFLAGS = '-march=native')
although this causes Stan to throw an error on a few processors.

Attaching package: 'coda'

The following object is masked from 'package:rstan':

    traceplot



In [2]:
# add path required by rstan
library(devtools) 
Sys.setenv(PATH = paste("C:/Rtools/bin", Sys.getenv("PATH"), sep=";")) 
Sys.setenv(PATH = paste("C:\\Rtools\\mingw_64\\bin", Sys.getenv("PATH"), sep=";")) 
Sys.setenv(BINPREF = "C:/Rtools/mingw_$(WIN)/bin/")

Loading required package: usethis


# Read csv into dataframe

In [3]:
dat.str <- Sys.glob("data.*.csv")
data <- as.data.frame(read.csv(file = dat.str))
# slicing training set (whole 2018 season)
dat <- data[data$period < 27,]

In [4]:
head(dat)

Date       home.name away.name home.number away.number round period
172 2019-04-07 FR        SK         6          15          3     26    
173 2019-04-07 HW        NM        10          12          3     26    
174 2019-04-07 WB        GC        17           7          3     26    
175 2019-04-06 BL        PA         2          13          3     26    
176 2019-04-06 CW        WC         4          18          3     26    
177 2019-04-06 GW        RI         9          14          3     26    
    home.score away.score home.goals ... Total.Score.Max Total.Score.Close
172  71        66         11         ... 168.5           168.5            
173  87        71         13         ... 180.5           180.5            
174  68        73          9         ... 170.5           170.5            
175 107        90         16         ... 178.5           178.5            
176  76        98         11         ... 166.5           165.5            
177 125        76         19         ... 166.5           166.5            
    Total.Score.Over.Open Total.Score.Over.Min Total.Score.Over.Max
172 1.89                  1.89                 1.91                
173 1.89                  1.89                 1.91                
174 1.89                  1.89                 1.91                
175 1.89                  1.89                 1.91                
176 1.89                  1.89                 1.89                
177 1.89                  1.89                 1.91                
    Total.Score.Over.Close Total.Score.Under.Open Total.Score.Under.Min
172 1.91                   1.89                   1.89                 
173 1.91                   1.89                   1.89                 
174 1.91                   1.89                   1.89                 
175 1.91                   1.89                   1.89                 
176 1.91                   1.89                   1.89                 
177 1.91                   1.89                   1.89                 
    Total.Score.Under.Max Total.Score.Under.Close
172 1.91                  1.91                   
173 1.91                  1.91                   
174 1.91                  1.91                   
175 1.91                  1.91                   
176 1.89                  1.91                   
177 1.91                  1.91

In [5]:
# library(hash)

# h <- hash()

# for (i in 1:length(sort(unique(dat$home.name)))){
#     h[[as.character(sort(unique(dat$home.name))[i])]] <- i
# }

In [82]:
# library(hash)

# h <- hash()

# for (i in 1:length(sort(unique(dat$home.name)))){
#     h[[as.character(sort(unique(dat$home.name))[i])]] <- i
# }

# home.number <- vector()
# away.number <- vector()

# for (i in 1:nrow(dat)){
#     home.number <- append(home.number, h[[as.character(dat$home.name[i])]])
#     away.number <- append(away.number, h[[as.character(dat$away.name[i])]])
    
# }

# dat$home.number <- home.number
# dat$away.number <- away.number

In [84]:
# write.csv(dat, 'temp.csv')

# 2019 Round 1 data

In [5]:
matchup <- data[data$period == 27,]
n.matches <- length(matchup$home.number)
matchup

Date       home.name away.name home.number away.number round period
163 2019-04-14 SK        HW        15          10          4     27    
164 2019-04-14 GC        CA         7           3          4     27    
165 2019-04-13 WC        FR        18           6          4     27    
166 2019-04-13 NM        AD        12           1          4     27    
167 2019-04-13 PA        RI        13          14          4     27    
168 2019-04-13 ES        BL         5           2          4     27    
169 2019-04-13 GE        GW         8           9          4     27    
170 2019-04-12 CW        WB         4          17          4     27    
171 2019-04-11 SY        ME        16          11          4     27    
    home.score away.score home.goals ... Total.Score.Max Total.Score.Close
163  74         69        10         ... 170.5           170.5            
164  59         57         8         ... 161.5           160.5            
165  69         56        10         ... 164.5           164.5            
166  71         59         9         ... 181.5           181.5            
167  92         99        14         ... 169.5           168.5            
168 112         65        17         ... 187.5           185.5            
169  75         79        11         ... 168.5           168.5            
170  78         64        11         ... 172.5           171.5            
171  78        100        11         ... 165.5           165.5            
    Total.Score.Over.Open Total.Score.Over.Min Total.Score.Over.Max
163 1.89                  1.89                 1.91                
164 1.89                  1.89                 1.89                
165 1.89                  1.89                 1.91                
166 1.89                  1.89                 1.91                
167 1.89                  1.89                 1.91                
168 1.87                  1.91                 1.89                
169 1.89                  1.89                 1.91                
170 1.89                  1.89                 1.91                
171 1.89                  1.89                 1.91                
    Total.Score.Over.Close Total.Score.Under.Open Total.Score.Under.Min
163 1.91                   1.89                   1.89                 
164 1.91                   1.89                   1.89                 
165 1.91                   1.89                   1.89                 
166 1.91                   1.89                   1.89                 
167 1.91                   1.89                   1.89                 
168 1.91                   1.91                   1.91                 
169 1.91                   1.89                   1.89                 
170 1.91                   1.89                   1.89                 
171 1.91                   1.89                   1.89                 
    Total.Score.Under.Max Total.Score.Under.Close
163 1.91                  1.91                   
164 1.89                  1.91                   
165 1.91                  1.91                   
166 1.91                  1.91                   
167 1.91                  1.91                   
168 1.89                  1.91                   
169 1.91                  1.91                   
170 1.91                  1.91                   
171 1.91                  1.91

# Data

In [6]:
home.name <- as.matrix(dat$home.name)
away.name <- as.matrix(dat$away.name)
home.numb <- dat$home.number
away.numb <- dat$away.number

home.Goals <- dat$home.goals
home.Behinds <- dat$home.behinds
away.Goals <- dat$away.goals
away.Behinds <- dat$away.behinds

period <- dat$period
n.teams <- 18
n.games <- length(home.numb)
n.periods <- max(period)
n.bps <- 2
bps <- c(1,24)

In [7]:
# matricies for the Owen paper centering
ones <- matrix(1, nrow = (n.teams-1), ncol = 1)
S_t <-  n.teams / (n.teams-1) * (diag(n.teams-1) + ones %*% t(ones))

# Jmat is n * n-1
J.up.left <- diag(n.teams-1) - (1/n.teams)*(ones %*% t(ones))
J.bot.left <- - t(ones) * 1/n.teams

Jmat <- rbind(J.up.left, J.bot.left)

# Store data into list required by STAN

In [8]:
dat.list <- list(N = n.teams,
                 G = n.games,
                 T = n.periods,
                 period = period,
                 home = home.numb,
                 away = away.numb,
                 homeGoals = home.Goals,
                 homeBehinds = home.Behinds,
                 awayGoals = away.Goals,
                 awayBehinds = away.Behinds,
                 BP = n.bps,
                 Breaks = bps,
                 Smat = S_t,
                 JmatTrans = t(Jmat),
                 N_Matches = n.matches,
                 nextHome = matchup$home.number,
                 nextAway = matchup$away.number)

# Compile the model

In [9]:
prefit <- stan("Skellam goal and behind difference.stan", data = dat.list, chains = 0)

DIAGNOSTIC(S) FROM PARSER:
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: assignment operator <- deprecated in the Stan language; use = instead.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # 

the number of chains is less than 1; sampling not done


# Sampling using MCMC (4 cores in parallel)

In [10]:
cl <- makeCluster(4)

clusterEvalQ(cl, library(rstan))

myfunction <- function(var1, var2, var3){
    stan(fit = var3, data = var2,
                            chains = 1, chain_id = var1, iter = 2500,
                            refresh = -1, init = "0")
}

sflist <- parLapply(cl, 1:4, fun = myfunction, var2 = dat.list, var3 = prefit)
stopCluster(cl)

[[1]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"       

[[2]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"       

[[3]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"       

[[4]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"

In [11]:
sflist

[[1]]
Inference for Stan model: Skellam goal and behind difference.
1 chains, each with iter=2500; warmup=1250; thin=1; 
post-warmup draws per chain=1250, total post-warmup draws=1250.

                           mean se_mean     sd   2.5%    25%    50%    75%
delta                      0.65    0.00   0.07   0.51   0.61   0.66   0.70
attackGoals_raw[1,1]       1.91    0.10   2.54  -3.27   0.21   2.10   3.70
attackGoals_raw[1,2]      -4.70    0.11   2.77  -8.87  -6.93  -5.00  -2.70
attackGoals_raw[1,3]      -3.54    0.12   3.32  -8.79  -6.17  -3.85  -1.09
attackGoals_raw[1,4]      -0.07    0.12   3.10  -6.24  -2.22  -0.04   2.04
attackGoals_raw[1,5]       0.51    0.11   2.64  -4.56  -1.24   0.44   2.21
attackGoals_raw[1,6]       1.01    0.10   2.79  -4.61  -0.93   1.11   2.93
attackGoals_raw[1,7]      -0.10    0.10   2.57  -5.12  -1.84  -0.10   1.54
attackGoals_raw[1,8]       1.38    0.13   2.66  -3.90  -0.50   1.42   3.27
attackGoals_raw[1,9]       1.37    0.06   1.92  -2.32   0.09   1

In [12]:
fit <- sflist2stanfit(sflist)

In [13]:
write.csv(print(summary(fit)), file = "fitproper.csv")

$summary
                                  mean      se_mean           sd          2.5%
delta                     6.522683e-01 0.0012814951 7.113334e-02  5.099029e-01
attackGoals_raw[1,1]      1.927563e+00 0.0516100182 2.647581e+00 -3.247643e+00
attackGoals_raw[1,2]     -4.768677e+00 0.0505591385 2.784031e+00 -8.914784e+00
attackGoals_raw[1,3]     -3.498243e+00 0.0726947116 3.356320e+00 -8.778252e+00
attackGoals_raw[1,4]     -8.061101e-02 0.0615861527 3.061505e+00 -6.270479e+00
attackGoals_raw[1,5]      5.982811e-01 0.0544048929 2.627433e+00 -4.415936e+00
attackGoals_raw[1,6]      9.786962e-01 0.0545876753 2.853078e+00 -4.702040e+00
attackGoals_raw[1,7]     -1.772914e-01 0.0532201975 2.541529e+00 -5.150002e+00
attackGoals_raw[1,8]      1.382904e+00 0.0568587642 2.698555e+00 -3.748536e+00
attackGoals_raw[1,9]      1.421687e+00 0.0532003596 1.960420e+00 -2.334843e+00
attackGoals_raw[1,10]     1.756726e+00 0.0419432762 2.219232e+00 -2.566565e+00
attackGoals_raw[1,11]    -2.895831e-01 0.05

# Extract parameters

In [14]:
fit.samples <- extract(fit)
write.csv(fit.samples, file = "samples.csv")

# Take the average of the mu for each team

In [15]:
# parameter estimate extractor
delta <- mean (fit.samples$delta)
muAttGoals.vec <- apply(fit.samples$muAttGoals, 2, mean) # I think the 18th team here is
  # suffering from the sum to zero constraint, maybe will dissapear with more samples

muAttBehinds.vec <- apply(fit.samples$muAttBehinds, 2, mean)
muDef.vec <- apply(fit.samples$muDef, 2, mean)

mu.ests <- matrix(c( "Goal attack mean estimates", muAttGoals.vec,"Behind attack mean estimates", muAttBehinds.vec,
                     "defend means estimates", muDef.vec), ncol = 3, byrow = F)
write.csv(mu.ests, file = "AR mean estimates.csv")

# Extract phiAtt, phiDef, attackGoals, attackBehinds, defend

In [16]:
phiAtt.vec <- mean(fit.samples$phiAtt)
phiDef.vec <- mean(fit.samples$phiDef)
std.attack.vec <- mean(fit.samples$stdAtt)
std.def.vec <- mean(fit.samples$stdDef)

goal.attack.strenghts.mat <- apply(fit.samples$attackGoals, 2:3, mean)
write.csv(goal.attack.strenghts.mat, file = "goal.attack.str.csv")

behind.attack.strengths.mat <- apply(fit.samples$attackBehinds, 2:3, mean)
write.csv(behind.attack.strengths.mat, file = "behind.attack.str.csv")

defence.strengths.mat <- apply(fit.samples$defend, 2:3, mean)
write.csv(defence.strengths.mat, file = "def.str.csv")

par.vec <- c(delta, "delta",
             phiAtt.vec, "phi.attack",
             phiDef.vec, "phi.defend",
             std.attack.vec, "std.attack",
             std.def.vec, "std.defend")

par.vec.est <- matrix(par.vec, ncol = 2, byrow = T)
write.csv(par.vec.est,  file = "parameter estimates.csv")

# Extract goalDiff, behindDiff, and totalDiff

In [17]:
avg.pred.goal.diff <- apply(fit.samples$goalDiff, 2, mean)
avg.pred.behind.diff <- apply(fit.samples$behindDiff, 2, mean)
avg.pred.total.diff <- apply(fit.samples$totalDiff, 2, mean)

In [18]:
# see if we got it right
actual.total.diff <- matchup$home.score - matchup$away.score
correct.vec <- ((avg.pred.total.diff * actual.total.diff)>0)

In [19]:
actual.total.diff
correct.vec

[1]   5   2  13  12  -7  47  -4  14 -22

[1]  TRUE  TRUE  TRUE  TRUE FALSE FALSE FALSE  TRUE FALSE

# Calculate percentage of win, loss and draw

In [20]:
# get the percentage of win/loss

winDrawLossPer <- function(x.vec) {
  home.win.per <- mean(as.numeric(x.vec > 0))
  draw.per <- mean(as.numeric(x.vec == 0))
  away.win.per <- mean(as.numeric(x.vec < 0))
  c(home.win.per, draw.per ,away.win.per)
}

In [21]:
per.chance.mat <- apply(fit.samples$totalDiff, 2, winDrawLossPer)
per.chance.mat

iterations [,1]   [,2]  [,3]   [,4]   [,5]   [,6]   [,7]   [,8]   [,9] 
      [1,] 0.7702 0.904 0.9528 0.5066 0.6696 0.4502 0.8690 0.6416 0.857
      [2,] 0.0272 0.027 0.0064 0.0510 0.0428 0.0372 0.0116 0.0860 0.010
      [3,] 0.2026 0.069 0.0408 0.4424 0.2876 0.5126 0.1194 0.2724 0.133

In [22]:
# the sd ests are going to be wildly larger than they should due to not throwing out burn in
# samples, should probably change all my apply's to deal with this but ehhhhhhhh, more samples
# takes care of it for the most part
sd.ests <- round(apply(fit.samples$totalDiff,2,sd),2)

In [23]:
sim.pred.mat <- matrix(c("behind diff", avg.pred.behind.diff,
                         "goal diff", avg.pred.goal.diff,
                         "total diff", avg.pred.total.diff,
                         "home team", as.character(matchup$home.name),
                         "away team", as.character(matchup$away.name),
                         "actual result", actual.total.diff,
                         "prediction correct?", correct.vec,
                         "home win prob", per.chance.mat[1,],
                         "draw prob", per.chance.mat[2,],
                         "home loss prob", per.chance.mat[3,],
                         "simulated sd ests", sd.ests
                         ), nrow = 11, byrow = T)

write.csv(sim.pred.mat, file = "internal predictions.csv")

In [24]:
sim.pred.mat

[,1]                [,2]    [,3]    [,4]     [,5]   [,6]    [,7]   
 [1,] behind diff         17.3442 8.0626  2.5002   4.7674 3.7362  5.4108 
 [2,] goal diff           0.6068  7.5798  38.3386  -0.636 1.9432  -1.7422
 [3,] total diff          20.985  53.5414 232.5318 0.9514 15.3954 -5.0424
 [4,] home team           SK      GC      WC       NM     PA      ES     
 [5,] away team           HW      CA      FR       AD     RI      BL     
 [6,] actual result       5       2       13       12     -7      47     
 [7,] prediction correct? TRUE    TRUE    TRUE     TRUE   FALSE   FALSE  
 [8,] home win prob       0.7702  0.904   0.9528   0.5066 0.6696  0.4502 
 [9,] draw prob           0.0272  0.027   0.0064   0.051  0.0428  0.0372 
[10,] home loss prob      0.2026  0.069   0.0408   0.4424 0.2876  0.5126 
[11,] simulated sd ests   52.3    103.36  356.98   43.89  43.21   45.68  
      [,8]     [,9]    [,10]  
 [1,] 1.4928   1.4612  -1.129 
 [2,] 19.0016  1.7714  14.2412
 [3,] 115.5024 12.0896 84.3182
 [4,] GE       CW      SY     
 [5,] GW       WB      ME     
 [6,] -4       14      -22    
 [7,] FALSE    TRUE    FALSE  
 [8,] 0.869    0.6416  0.857  
 [9,] 0.0116   0.086   0.01   
[10,] 0.1194   0.2724  0.133  
[11,] 224.57   37.09   162.54